Resources Used
- wget.download('https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/_downloads/da4babe668a8afb093cc7776d7e630f3/generate_tfrecord.py')
- Setup https://tensorflow-object-detection-api-tutorial.readthedocs.io/en/latest/install.html

# 0. Setup Paths

In [21]:
WORKSPACE_PATH = 'Tensorflow/workspace'
SCRIPTS_PATH = 'Tensorflow/scripts'
APIMODEL_PATH = 'Tensorflow/models'
ANNOTATION_PATH = WORKSPACE_PATH+'/annotations'
IMAGE_PATH = WORKSPACE_PATH+'/images'
MODEL_PATH = WORKSPACE_PATH+'/models'
PRETRAINED_MODEL_PATH = WORKSPACE_PATH+'/pre-trained-models'
CONFIG_PATH = MODEL_PATH+'/my_ssd_mobnet/pipeline.config'
CHECKPOINT_PATH = MODEL_PATH+'/my_ssd_mobnet/'

# 1. Create Label Map

In [2]:
labels = [{'name':'ExcuseMe', 'id':1}, {'name':'Hello', 'id':2}, {'name':'Help', 'id':3}, {'name':'ItisCool', 'id':4},
          {'name':'ItisWarm', 'id':5}, {'name':'No', 'id':6}, {'name':'Please', 'id':7}, {'name':'Sorry', 'id':8}, {'name':'Stop', 'id':9},
          {'name':'Thankyou', 'id':10}, {'name':'What', 'id':11}, {'name':'Yes', 'id':12}]

with open(ANNOTATION_PATH + '\label_map.pbtxt', 'w') as f:
    for label in labels:
        f.write('item { \n')
        f.write('\tname:\'{}\'\n'.format(label['name']))
        f.write('\tid:{}\n'.format(label['id']))
        f.write('}\n')

# 2. Create TF records

In [11]:
!python {SCRIPTS_PATH + '/generate_tfrecord.py'} -x {IMAGE_PATH + '/train'} -l {ANNOTATION_PATH + '/label_map.pbtxt'} -o {ANNOTATION_PATH + '/train.record'}
!python {SCRIPTS_PATH + '/generate_tfrecord.py'} -x{IMAGE_PATH + '/test'} -l {ANNOTATION_PATH + '/label_map.pbtxt'} -o {ANNOTATION_PATH + '/test.record'}

Successfully created the TFRecord file: Tensorflow/workspace/annotations/train.record
Successfully created the TFRecord file: Tensorflow/workspace/annotations/test.record


# 3. Download TF Models Pretrained Models from Tensorflow Model Zoo

In [24]:
!cd Tensorflow && git clone https://github.com/tensorflow/models

fatal: destination path 'models' already exists and is not an empty directory.


In [13]:
#wget.download('http://download.tensorflow.org/models/object_detection/tf2/20200711/ssd_mobilenet_v2_fpnlite_320x320_coco17_tpu-8.tar.gz')
#!mv ssd_mobilenet_v2_fpnlite_320x320_coco17_tpu-8.tar.gz {PRETRAINED_MODEL_PATH}
#!cd {PRETRAINED_MODEL_PATH} && tar -zxvf ssd_mobilenet_v2_fpnlite_320x320_coco17_tpu-8.tar.gz

# 4. Copy Model Config to Training Folder

In [24]:
CUSTOM_MODEL_NAME = 'my_ssd_mobnet' 

In [26]:
!mkdir {'Tensorflow\workspace\models\\'+CUSTOM_MODEL_NAME}
!cp {PRETRAINED_MODEL_PATH+'/ssd_mobilenet_v2_fpnlite_320x320_coco17_tpu-8/pipeline.config'} {MODEL_PATH+'/'+CUSTOM_MODEL_NAME}

# 5. Update Config For Transfer Learning

In [25]:
import tensorflow as tf
from object_detection.utils import config_util
from object_detection.protos import pipeline_pb2
from google.protobuf import text_format

In [26]:
CONFIG_PATH = MODEL_PATH+'/'+CUSTOM_MODEL_NAME+'/pipeline.config'

In [27]:
config = config_util.get_configs_from_pipeline_file(CONFIG_PATH)

In [28]:
config

{'model': ssd {
   num_classes: 12
   image_resizer {
     fixed_shape_resizer {
       height: 320
       width: 320
     }
   }
   feature_extractor {
     type: "ssd_mobilenet_v2_fpn_keras"
     depth_multiplier: 1.0
     min_depth: 16
     conv_hyperparams {
       regularizer {
         l2_regularizer {
           weight: 3.9999998989515007e-05
         }
       }
       initializer {
         random_normal_initializer {
           mean: 0.0
           stddev: 0.009999999776482582
         }
       }
       activation: RELU_6
       batch_norm {
         decay: 0.996999979019165
         scale: true
         epsilon: 0.0010000000474974513
       }
     }
     use_depthwise: true
     override_base_feature_extractor_hyperparams: true
     fpn {
       min_level: 3
       max_level: 7
       additional_layer_depth: 128
     }
   }
   box_coder {
     faster_rcnn_box_coder {
       y_scale: 10.0
       x_scale: 10.0
       height_scale: 5.0
       width_scale: 5.0
     }
   }
   matc

In [29]:
pipeline_config = pipeline_pb2.TrainEvalPipelineConfig()
with tf.io.gfile.GFile(CONFIG_PATH, "r") as f:                                                                                                                                                                                                                     
    proto_str = f.read()                                                                                                                                                                                                                                          
    text_format.Merge(proto_str, pipeline_config)  

In [30]:
pipeline_config.model.ssd.num_classes = 12
pipeline_config.train_config.batch_size = 4
pipeline_config.train_config.fine_tune_checkpoint = PRETRAINED_MODEL_PATH+'/ssd_mobilenet_v2_fpnlite_320x320_coco17_tpu-8/checkpoint/ckpt-0'
pipeline_config.train_config.fine_tune_checkpoint_type = "detection"
pipeline_config.train_input_reader.label_map_path= ANNOTATION_PATH + '/label_map.pbtxt'
pipeline_config.train_input_reader.tf_record_input_reader.input_path[:] = [ANNOTATION_PATH + '/train.record']
pipeline_config.eval_input_reader[0].label_map_path = ANNOTATION_PATH + '/label_map.pbtxt'
pipeline_config.eval_input_reader[0].tf_record_input_reader.input_path[:] = [ANNOTATION_PATH + '/test.record']

In [10]:
config_text = text_format.MessageToString(pipeline_config)                                                                                                                                                                                                        
with tf.io.gfile.GFile(CONFIG_PATH, "wb") as f:                                                                                                                                                                                                                     
    f.write(config_text)   

# 6. Train the model

In [34]:
print("""python {}/research/object_detection/model_main_tf2.py --model_dir={}/{} --pipeline_config_path={}/{}/pipeline.config --num_train_steps=20000""".format(APIMODEL_PATH, MODEL_PATH,CUSTOM_MODEL_NAME,MODEL_PATH,CUSTOM_MODEL_NAME))

python Tensorflow/models/research/object_detection/model_main_tf2.py --model_dir=Tensorflow/workspace/models/my_ssd_mobnet --pipeline_config_path=Tensorflow/workspace/models/my_ssd_mobnet/pipeline.config --num_train_steps=20000


# 7. Load Train Model From Checkpoint

In [31]:
import os
from object_detection.utils import label_map_util
from object_detection.utils import visualization_utils as viz_utils
from object_detection.builders import model_builder

In [32]:
# Load pipeline config and build a detection model
configs = config_util.get_configs_from_pipeline_file(CONFIG_PATH)
detection_model = model_builder.build(model_config=configs['model'], is_training=False)

# Restore checkpoint
ckpt = tf.compat.v2.train.Checkpoint(model=detection_model)
ckpt.restore(os.path.join(CHECKPOINT_PATH, 'ckpt-20')).expect_partial()

@tf.function
def detect_fn(image):
    image, shapes = detection_model.preprocess(image)
    prediction_dict = detection_model.predict(image, shapes)
    detections = detection_model.postprocess(prediction_dict, shapes)
    return detections

# 8. Detect in Real-Time

In [33]:
import cv2 
import numpy as np
import time

In [34]:
category_index = label_map_util.create_category_index_from_labelmap(ANNOTATION_PATH+'/label_map.pbtxt')

In [35]:
category_index

{1: {'id': 1, 'name': 'ExcuseMe'},
 2: {'id': 2, 'name': 'Hello'},
 3: {'id': 3, 'name': 'Help'},
 4: {'id': 4, 'name': 'ItisCool'},
 5: {'id': 5, 'name': 'ItisWarm'},
 6: {'id': 6, 'name': 'No'},
 7: {'id': 7, 'name': 'Please'},
 8: {'id': 8, 'name': 'Sorry'},
 9: {'id': 9, 'name': 'Stop'},
 10: {'id': 10, 'name': 'Thankyou'},
 11: {'id': 11, 'name': 'What'},
 12: {'id': 12, 'name': 'Yes'}}

In [39]:
cap.release()

In [37]:
# Setup capture
cap = cv2.VideoCapture(0)
history = []
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

In [38]:
cap = cv2.VideoCapture(0)
history = []
while True: 
    ret, frame = cap.read()
    image_np = np.array(frame)
    
    input_tensor = tf.convert_to_tensor(np.expand_dims(image_np, 0), dtype=tf.float32)
    detections = detect_fn(input_tensor)
    
    num_detections = int(detections.pop('num_detections'))
    detections = {key: value[0, :num_detections].numpy()
                  for key, value in detections.items()}
    detections['num_detections'] = num_detections

    # detection_classes should be ints.
    detections['detection_classes'] = detections['detection_classes'].astype(np.int64)

    label_id_offset = 1
    image_np_with_detections = image_np.copy()

    viz_utils.visualize_boxes_and_labels_on_image_array(
                image_np_with_detections,
                detections['detection_boxes'],
                detections['detection_classes']+label_id_offset,
                detections['detection_scores'],
                category_index,
                use_normalized_coordinates=True,
                max_boxes_to_draw=5,
                min_score_thresh=.5,
                agnostic_mode=False)

    cv2.imshow('object detection',  cv2.resize(image_np_with_detections, (800, 600)))
    
    word = category_index[detections['detection_classes'][np.argmax(detections['detection_scores'])]+1]['name']
    history.append(word)
    #time.sleep(2)
    print(history)
    
    if cv2.waitKey(1) & 0xFF == ord('q'):
        cap.release()
        break

['Thankyou']
['Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Th

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', '

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'T

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'T

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Yes', 'Sorry']
['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou'

...

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Yes', 'Sorry', 'Sorry', 'Sorry', 'Hello', 'Hello', 'Thankyou', 'Hello', 'T

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Yes', 'Sorry', 'Sorry', 'Sorry', 'Hello', 'Hello', 'Thankyou', 'Hello', 'T

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Yes', 'Sorry', 'Sorry', 'Sorry', 'Hello', 'Hello', 'Thankyou', 'Hello', 'T

['Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Thankyou', 'Yes', 'Sorry', 'Sorry', 'Sorry', 'Hello', 'Hello', 'Thankyou', 'Hello', 'T

KeyboardInterrupt: 

In [15]:
history

['Hello',
 'Help',
 'It is Cool',
 'It is Warm',
 'No',
 'PleaseSorry',
 'Stop',
 'Thank you',
 'What',
 'Yes']

In [16]:
type(history)

list

In [17]:
out_str = " "
history1 = out_str.join(history)

In [18]:
history1

'Hello Help It is Cool It is Warm No PleaseSorry Stop Thank you What Yes'

In [19]:
type(history1)

str

In [20]:
# Import the Gtts module for text  
# to speech conversion 
from gtts import gTTS 
  
# import Os module to start the audio file
import os 
  
#mytext = 'Convert this Text to Speech in Python'
  
# Language we want to use 
language = 'en'
  

myobj = gTTS(text=history1, lang=language, slow=True ) 
  

myobj.save("output.mp3") 
  
# Play the converted file 
os.system("start output.mp3") 

0